In [ ]:
import os
import glob
import json
import pytz
import nltk
nltk.download('punkt')
import numpy as np
import pandas as pd
import dateutil.parser
from textblob import TextBlob
from datetime import datetime
import matplotlib.pyplot as plt

In [ ]:
news_path = '../Data/News/'
stock_path = '../Data/CHARTS/'

### Parsing news data
Read news json files and index by time stamp. Stored in news_df DataFrame. Relative path of each json file stored in DF. Access text via json['text'] key. TimeStamp converted to Eastern.

In [ ]:
def filtertext(text, stock, company):
    filteredsentences = set()
    sentences = text.split('.')
    LEN = len(sentences)
    for i in range(LEN):
        sentence = sentences[i].lower()
        #print(i, LEN)
        if (stock in sentence) or (company in sentence):
            filteredsentences.add(sentences[i])
            if i < 2:
                if i+1<LEN:
                    filteredsentences.add(sentences[i+1])
                if i+2<LEN:
                    filteredsentences.add(sentences[i+2])
            elif i>=2 and i<LEN-2:
                filteredsentences.add(sentences[i-2])
                filteredsentences.add(sentences[i-1])
                filteredsentences.add(sentences[i+1])
                filteredsentences.add(sentences[i+2])
            elif i>=LEN-2:
                filteredsentences.add(sentences[i-2])
                filteredsentences.add(sentences[i-1])
    return list(filteredsentences)
'''
def filteramzn(text):
    filteredsentences = set()
    sentences = text.split('.')
    for i in range(len(sentences)):
        sentence = sentences[i].lower()
        if (stock in sentence) or (company in sentence):
            filteredsentences.add(sentences[i])
            if i < 2:
                if i+1<len(sentences):
                    filteredsentences.add(sentences[i+1])
                if i+2<len(sentences):
                    filteredsentences.add(sentences[i+2])
            elif i>=2 and i<len(sentences)-2:
                filteredsentences.add(sentences[i-2])
                filteredsentences.add(sentences[i-1])
                filteredsentences.add(sentences[i+1])
                filteredsentences.add(sentences[i+2])
            elif i>len(sentences)-2:
                filteredsentences.add(sentences[i-2])
                filteredsentences.add(sentences[i-1])
                filteredsentences.add(sentences[i])
    return list(filteredsentences)
'''

def sentiment(text):
    if text!=[]:
        
        sentiments = []
        for sentence in text:
            blob = TextBlob(sentence)
            ngrams = blob.ngrams(n=3)
            for ngram in ngrams:
                ngram = TextBlob(str(ngram))
                sentiments.append(ngram.sentiment.polarity)
        if len(sentiments) != 0: #articles with mandarin return a zero element sentiment array
            return (sum(sentiments)/len(sentiments))
        else:
            return 0
    else:
        return 0

In [ ]:
times = []
text = []
news_file_loc = []
sites = []
organizations = []
titles = []
time_zone = pytz.timezone('US/Eastern')
json_files = glob.glob(news_path + '*/*.json')
print(len(json_files))
for news in json_files:
    with open(news, 'r') as f:
        d = json.load(f)
        iso_time = dateutil.parser.isoparse(d['published']).astimezone(time_zone)
        times.append(iso_time)
        news_file_loc.append(news)
        text.append(d['text'])
        sites.append(d['thread']['site'])
        titles.append(d['title'])

In [ ]:
news

In [ ]:
news_df = pd.DataFrame({'timestamp': times, 'text': text, 'site': sites, 'news_file_loc': news_file_loc })

In [ ]:
news_df['filteredtext_aapl'] = news_df['text'].apply(filtertext, args=('aapl', 'apple'))
news_df['filteredtext_amzn'] = news_df['text'].apply(filtertext, args=('amzn', 'amazon'))
news_df['aapl_sentiment'] = news_df['filteredtext_aapl'].apply(sentiment)
news_df['amzn_sentiment'] = news_df['filteredtext_amzn'].apply(sentiment)

In [ ]:
news_df

In [ ]:
news_df.to_csv('../Data/news_df.csv')

### After imports and Functions, run from here

In [ ]:
news_df = pd.read_csv('../Data/news_df_with_aapl_amzn_sentiment.csv')

In [ ]:
def clean_ascii(text):
    cleaned_str =  ''.join(i for i in text if ord(i)<128)
    if len(cleaned_str) > 0.7*len(text):
        return cleaned_str
    return []

In [ ]:
news_df['filteredtext_aapl'] = news_df['filteredtext_aapl'].apply(clean_ascii)
news_df['filteredtext_amzn'] = news_df['filteredtext_amzn'].apply(clean_ascii)
news_df

In [ ]:
news_df[news_df['filteredtext_amzn'].astype(str) != '[]']

In [ ]:
news_df['gmt_timestamp'] = pd.to_datetime(news_df['timestamp']).apply(lambda x: np.datetime64(x))
news_df = news_df.sort_values(by=['timestamp'])
news_df.index = (range(news_df.shape[0]))
#del news_df['Unnamed: 0']
news_df

### Reading CHARTS stock data
Timezone converted. Example done for APPLE240, change accordingly.

In [576]:
headers = ['date', 'time', 'open', 'close', 'low', 'high', 'volume']
df = pd.read_csv(stock_path + "APPLE240.csv", header=None, names = headers)
df['timestamp'] = pd.to_datetime(df['date'] + ' ' + df['time']).dt.tz_localize(time_zone)
df['gmt_timestamp'] = df['timestamp'].apply(lambda x: np.datetime64(x))
df['label'] = df['open'] - df['open'].shift(1)
df = df.dropna(axis=0)
df['label'] = df['label'].apply(lambda x: -1 if x<0 else 1)
del df['date'], df['time']

/home/adnaks/.local/lib/python3.6/site-packages/ipykernel_launcher.py:4: DeprecationWarning: parsing timezone aware datetimes is deprecated; this will raise an error in the future
  after removing the cwd from sys.path.


In [577]:
df.head()

open   close     low    high  volume                 timestamp  \
1  93.661  94.194  93.420  93.460    1512 2014-06-30 17:30:00-04:00   
2  93.973  94.546  93.611  94.546    3405 2014-07-01 13:30:00-04:00   
3  94.536  94.546  93.993  93.993    1382 2014-07-01 17:30:00-04:00   
4  94.344  94.515  93.791  94.043    3249 2014-07-02 13:30:00-04:00   
5  94.053  94.053  93.540  93.902    1227 2014-07-02 17:30:00-04:00   

        gmt_timestamp  label  
1 2014-06-30 21:30:00      1  
2 2014-07-01 17:30:00      1  
3 2014-07-01 21:30:00      1  
4 2014-07-02 17:30:00     -1  
5 2014-07-02 21:30:00     -1

In [578]:
df['timestamp']

1      2014-06-30 17:30:00-04:00
2      2014-07-01 13:30:00-04:00
3      2014-07-01 17:30:00-04:00
4      2014-07-02 13:30:00-04:00
5      2014-07-02 17:30:00-04:00
                  ...           
3241   2019-01-31 13:30:00-05:00
3242   2019-01-31 17:30:00-05:00
3243   2019-01-31 21:30:00-05:00
3244   2019-02-01 13:30:00-05:00
3245   2019-02-01 17:30:00-05:00
Name: timestamp, Length: 3245, dtype: datetime64[ns, US/Eastern]

In [579]:
start = news_df['gmt_timestamp'][0]

In [580]:
news_df.columns

Index(['timestamp', 'site', 'news_file_loc', 'filteredtext_aapl',
       'filteredtext_amzn', 'aapl_sentiment', 'amzn_sentiment',
       'gmt_timestamp', 'stock_time'],
      dtype='object')

In [581]:
df = df[df['gmt_timestamp'] >= start]

In [582]:
df.index = range(df.shape[0])
df['gmt_timestamp']

0     2017-12-07 22:30:00
1     2017-12-08 02:30:00
2     2017-12-08 18:30:00
3     2017-12-08 22:30:00
4     2017-12-11 18:30:00
              ...        
798   2019-01-31 18:30:00
799   2019-01-31 22:30:00
800   2019-02-01 02:30:00
801   2019-02-01 18:30:00
802   2019-02-01 22:30:00
Name: gmt_timestamp, Length: 803, dtype: datetime64[ns]

In [583]:
end  = np.datetime64(df['gmt_timestamp'][0])
news_times = news_df['gmt_timestamp'].values
#end = pd.to_datetime(end)

In [584]:
i=0; k=-1
stock_times = []
for i,time in enumerate(news_times):
    #time = np.datetime64(time)
    if time <= end:
        stock_times.append(end)
        print (time, end)
        #break
        #pass
    else:
        k = k+1
        temp = df['gmt_timestamp'].values[k]
        while(time > temp):
            k = k+1
            #start = df['timestamp'].values[k]
            temp  = df['gmt_timestamp'].values[k]
        end = temp
        stock_times.append(end)
        print (time, end)
    #print (time, end)
    #stock_times.append(end)
        

2017-12-07T20:00:00.000000000 2017-12-07T22:30:00.000000
2017-12-08T21:37:00.000000000 2017-12-08T22:30:00.000000000
2017-12-12T01:55:00.000000000 2017-12-12T02:30:00.000000000
2017-12-12T22:10:00.000000000 2017-12-12T22:30:00.000000000
2017-12-14T11:42:00.000000000 2017-12-14T18:30:00.000000000
2017-12-14T12:31:00.000000000 2017-12-14T18:30:00.000000000
2017-12-15T02:32:00.000000000 2017-12-15T18:30:00.000000000
2017-12-15T12:04:00.000000000 2017-12-15T18:30:00.000000000
2017-12-18T20:05:00.000000000 2017-12-18T22:30:00.000000000
2017-12-21T00:00:00.000000000 2017-12-21T02:30:00.000000000
2017-12-21T00:00:00.000000000 2017-12-21T02:30:00.000000000
2017-12-21T00:00:00.000000000 2017-12-21T02:30:00.000000000
2017-12-21T00:00:00.000000000 2017-12-21T02:30:00.000000000
2017-12-21T00:00:00.000000000 2017-12-21T02:30:00.000000000
2017-12-21T00:00:00.000000000 2017-12-21T02:30:00.000000000
2017-12-21T00:00:00.000000000 2017-12-21T02:30:00.000000000
2017-12-21T02:25:00.000000000 2017-12-21T02

2018-01-10T22:30:00.000000000 2018-01-10T22:30:00.000000000
2018-01-10T22:30:00.000000000 2018-01-10T22:30:00.000000000
2018-01-10T22:30:00.000000000 2018-01-10T22:30:00.000000000
2018-01-10T22:38:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T22:44:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T22:44:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T22:45:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T22:48:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T22:53:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T22:57:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T23:05:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T23:20:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T23:22:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T23:38:00.000000000 2018-01-11T02:30:00.000000000
2018-01-10T23:48:00.000000000 2018-01-11T02:30:00.000000000
2018-01-11T00:00:00.000000000 2018-01-11T02:30:00.000000000
2018-01-11T00:00:00.000000000 2018-01-11

2018-01-22T17:50:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T17:54:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T17:54:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T17:58:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T17:58:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T17:58:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T17:59:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T18:02:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T18:07:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T18:08:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T18:08:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T18:11:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T18:30:00.000000000 2018-01-22T18:30:00.000000000
2018-01-22T18:31:00.000000000 2018-01-22T22:30:00.000000000
2018-01-22T18:31:00.000000000 2018-01-22T22:30:00.000000000
2018-01-22T18:45:00.000000000 2018-01-22T22:30:00.000000000
2018-01-22T18:59:00.000000000 2018-01-22

2018-01-31T03:24:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T03:40:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T03:55:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T04:00:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T04:33:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T05:00:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T05:00:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T05:00:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T05:00:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T05:00:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T05:04:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T05:52:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T06:12:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T06:27:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T06:28:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T06:28:00.000000000 2018-01-31T18:30:00.000000000
2018-01-31T06:49:00.000000000 2018-01-31

2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08T02:30:00.000000000
2018-02-08T00:00:00.000000000 2018-02-08

...

2018-12-26T14:41:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:47:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:47:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:47:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:47:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:49:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:52:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:53:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T14:59:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T15:00:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T15:00:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T15:04:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T15:12:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T15:43:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T15:51:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T16:00:00.000000000 2018-12-26T18:30:00.000000000
2018-12-26T16:03:00.000000000 2018-12-26

2019-01-03T16:05:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:07:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:08:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:09:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:09:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:10:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:10:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:11:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:13:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:13:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:15:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:18:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:19:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:20:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:21:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:22:00.000000000 2019-01-03T18:30:00.000000000
2019-01-03T16:22:00.000000000 2019-01-03

2019-01-08T16:49:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T16:51:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T16:56:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T16:57:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:01:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:03:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:06:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:09:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:12:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:12:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:12:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:16:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:27:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:37:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:42:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:42:00.000000000 2019-01-08T18:30:00.000000000
2019-01-08T17:48:00.000000000 2019-01-08

2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17T02:30:00.000000000
2019-01-17T00:00:00.000000000 2019-01-17

2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29T02:30:00.000000000
2019-01-29T00:00:00.000000000 2019-01-29

In [585]:
len(stock_times)

76989

In [586]:
end

numpy.datetime64('2019-02-01T22:30:00.000000000')

In [587]:
news_times[i]

numpy.datetime64('2019-02-01T22:28:00.000000000')

In [588]:
stock_times[-1]

numpy.datetime64('2019-02-01T22:30:00.000000000')

In [589]:
news_df['gmt_timestamp']

0       2017-12-07 20:00:00
1       2017-12-08 21:37:00
2       2017-12-12 01:55:00
3       2017-12-12 22:10:00
4       2017-12-14 11:42:00
                ...        
76984   2019-02-01 21:28:00
76985   2019-02-01 21:34:00
76986   2019-02-01 21:51:00
76987   2019-02-01 22:09:00
76988   2019-02-01 22:28:00
Name: gmt_timestamp, Length: 76989, dtype: datetime64[ns]

In [590]:
df.shape

(803, 8)

In [591]:
df.iloc[-1]['gmt_timestamp']

Timestamp('2019-02-01 22:30:00')

In [592]:
news_df = news_df[news_df.gmt_timestamp < df.iloc[-1]['gmt_timestamp']]

In [593]:
news_df['stock_time'] = stock_times

In [594]:
news_df[news_df.gmt_timestamp > news_df.stock_time]

Empty DataFrame
Columns: [timestamp, site, news_file_loc, filteredtext_aapl, filteredtext_amzn, aapl_sentiment, amzn_sentiment, gmt_timestamp, stock_time]
Index: []

In [ ]:
news_df

In [595]:
final_df = news_df.merge(df, left_on='stock_time', right_on='gmt_timestamp')

In [596]:
final_df.head()

timestamp_x               site  \
0  2017-12-07 15:00:00-05:00   businesswire.com   
1  2017-12-08 16:37:00-05:00          yahoo.com   
2  2017-12-11 20:55:00-05:00          yahoo.com   
3  2017-12-12 17:10:00-05:00  investingnews.com   
4  2017-12-14 06:42:00-05:00   seekingalpha.com   

                            news_file_loc  \
0  ../Data/News/2018-01/news_0000265.json   
1  ../Data/News/2018-01/news_0001827.json   
2  ../Data/News/2018-01/news_0000282.json   
3  ../Data/News/2018-01/news_0001849.json   
4  ../Data/News/2018-01/news_0001855.json   

                                   filteredtext_aapl filteredtext_amzn  \
0  ['\nNAPE Summit Week will also feature the ann...                []   
1  ['\niPhone X  Best phone if money isnt an issu...                []   
2  ['', ' They are not just the largest browser, ...                []   
3  [' Cobalt is under increasing supply pressure ...                []   
4  [" Cramer prefers Finisar (NASDAQ: FNSR ) afte...                []   

   aapl_sentiment  amzn_sentiment     gmt_timestamp_x          stock_time  \
0        0.033822             0.0 2017-12-07 20:00:00 2017-12-07 22:30:00   
1        0.132289             0.0 2017-12-08 21:37:00 2017-12-08 22:30:00   
2        0.026471             0.0 2017-12-12 01:55:00 2017-12-12 02:30:00   
3        0.025117             0.0 2017-12-12 22:10:00 2017-12-12 22:30:00   
4        0.037500             0.0 2017-12-14 11:42:00 2017-12-14 18:30:00   

     open   close     low    high  volume               timestamp_y  \
0  169.73  170.43  168.93  169.29   28528 2017-12-07 17:30:00-05:00   
1  169.98  170.05  168.79  169.31   24782 2017-12-08 17:30:00-05:00   
2  172.61  172.80  172.59  172.67      90 2017-12-11 21:30:00-05:00   
3  171.78  172.14  171.55  171.70   21640 2017-12-12 17:30:00-05:00   
4  172.41  173.12  171.63  172.14   24351 2017-12-14 13:30:00-05:00   

      gmt_timestamp_y  label  
0 2017-12-07 22:30:00      1  
1 2017-12-08 22:30:00      1  
2 2017-12-12 02:30:00      1  
3 2017-12-12 22:30:00     -1  
4 2017-12-14 18:30:00      1

In [597]:
del final_df['timestamp_x'], final_df['timestamp_y'], final_df['gmt_timestamp_y']

In [598]:
column_list = list(final_df.columns)

In [599]:
for i,name in enumerate(column_list):
    if name == 'gmt_timestamp_x':
        column_list[i] = 'news_timestamp'

In [600]:
final_df.columns = column_list

In [601]:
final_df

site                           news_file_loc  \
0             businesswire.com  ../Data/News/2018-01/news_0000265.json   
1                    yahoo.com  ../Data/News/2018-01/news_0001827.json   
2                    yahoo.com  ../Data/News/2018-01/news_0000282.json   
3            investingnews.com  ../Data/News/2018-01/news_0001849.json   
4             seekingalpha.com  ../Data/News/2018-01/news_0001855.json   
...                        ...                                     ...   
76984         tickerreport.com  ../Data/News/2019-02/news_0000928.json   
76985       highlightpress.com  ../Data/News/2019-02/news_0000423.json   
76986                yahoo.com  ../Data/News/2019-02/news_0000529.json   
76987                yahoo.com  ../Data/News/2019-02/news_0000915.json   
76988  dakotafinancialnews.com  ../Data/News/2019-02/news_0000944.json   

                                       filteredtext_aapl filteredtext_amzn  \
0      ['\nNAPE Summit Week will also feature the ann...                []   
1      ['\niPhone X  Best phone if money isnt an issu...                []   
2      ['', ' They are not just the largest browser, ...                []   
3      [' Cobalt is under increasing supply pressure ...                []   
4      [" Cramer prefers Finisar (NASDAQ: FNSR ) afte...                []   
...                                                  ...               ...   
76984  ['00 price target on shares of Apple in a rese...                []   
76985  ['4% in the 2nd quarter', ' Finally, Citigroup...                []   
76986  ['\nFacebook ha tenido que lidiar con los escn...                []   
76987  [' and China flags side by side with a graph t...                []   
76988  ['\nApple (NASDAQ:AAPL) last issued its quarte...                []   

       aapl_sentiment  amzn_sentiment      news_timestamp          stock_time  \
0            0.033822             0.0 2017-12-07 20:00:00 2017-12-07 22:30:00   
1            0.132289             0.0 2017-12-08 21:37:00 2017-12-08 22:30:00   
2            0.026471             0.0 2017-12-12 01:55:00 2017-12-12 02:30:00   
3            0.025117             0.0 2017-12-12 22:10:00 2017-12-12 22:30:00   
4            0.037500             0.0 2017-12-14 11:42:00 2017-12-14 18:30:00   
...               ...             ...                 ...                 ...   
76984        0.007242             0.0 2019-02-01 21:28:00 2019-02-01 22:30:00   
76985        0.004206             0.0 2019-02-01 21:34:00 2019-02-01 22:30:00   
76986        0.000000             0.0 2019-02-01 21:51:00 2019-02-01 22:30:00   
76987        0.018403             0.0 2019-02-01 22:09:00 2019-02-01 22:30:00   
76988        0.001992             0.0 2019-02-01 22:28:00 2019-02-01 22:30:00   

         open   close     low    high  volume  label  
0      169.73  170.43  168.93  169.29   28528      1  
1      169.98  170.05  168.79  169.31   24782      1  
2      172.61  172.80  172.59  172.67      90      1  
3      171.78  172.14  171.55  171.70   21640     -1  
4      172.41  173.12  171.63  172.14   24351      1  
...       ...     ...     ...     ...     ...    ...  
76984  167.14  167.42  165.90  166.12   21342      1  
76985  167.14  167.42  165.90  166.12   21342      1  
76986  167.14  167.42  165.90  166.12   21342      1  
76987  167.14  167.42  165.90  166.12   21342      1  
76988  167.14  167.42  165.90  166.12   21342      1  

[76989 rows x 14 columns]

In [602]:
final_df[final_df['label'] == 1].shape

(37532, 14)

In [627]:
final_df.stock_time

0       2017-12-07 22:30:00
1       2017-12-08 22:30:00
2       2017-12-12 02:30:00
3       2017-12-12 22:30:00
4       2017-12-14 18:30:00
                ...        
76984   2019-02-01 22:30:00
76985   2019-02-01 22:30:00
76986   2019-02-01 22:30:00
76987   2019-02-01 22:30:00
76988   2019-02-01 22:30:00
Name: stock_time, Length: 76989, dtype: datetime64[ns]

In [604]:
final_df.to_csv('../Data/final_dataset_joined.csv')

In [628]:
res = final_df.groupby('stock_time')

In [655]:
d = (res['filteredtext_aapl'].first()).to_dict()

In [632]:
final_df['stock_time'].unique().shape

(779,)

In [677]:
keys = final_df['stock_time'].unique()

In [686]:
lst = res.get_group(keys[700])['filteredtext_aapl'].to_list()

In [689]:
d = dict()
for k in keys:
    d[k] = res.get_group(keys[700])['filteredtext_aapl'].to_list()

In [692]:
d[d.keys()[0]]

TypeError: 'dict_keys' object does not support indexing